In [1]:
## IMPORTS
import numpy as np
import pandas as pd
from datetime import date
import yahoo_fin.stock_info as yf
from stage import getStage, fullPrint

In [2]:
today = date.today()
today = today.strftime('%Y-%m-%d')
transaction = yf.get_data('AAPL', start_date="1995-01-02",end_date="2022-01-09", index_as_date = True, interval="1wk").drop(['open','high','low','close','adjclose','volume','ticker'],axis=1)
transaction['holding'] = np.empty((len(transaction), 0)).tolist()
fullPrint(transaction)

           holding
1995-01-02      []
1995-01-09      []
1995-01-16      []
1995-01-23      []
1995-01-30      []
1995-02-06      []
1995-02-13      []
1995-02-20      []
1995-02-27      []
1995-03-06      []
1995-03-13      []
1995-03-20      []
1995-03-27      []
1995-04-03      []
1995-04-10      []
1995-04-17      []
1995-04-24      []
1995-05-01      []
1995-05-08      []
1995-05-15      []
1995-05-22      []
1995-05-29      []
1995-06-05      []
1995-06-12      []
1995-06-19      []
1995-06-26      []
1995-07-03      []
1995-07-10      []
1995-07-17      []
1995-07-24      []
1995-07-31      []
1995-08-07      []
1995-08-14      []
1995-08-21      []
1995-08-28      []
1995-09-04      []
1995-09-11      []
1995-09-18      []
1995-09-25      []
1995-10-02      []
1995-10-09      []
1995-10-16      []
1995-10-23      []
1995-10-30      []
1995-11-06      []
1995-11-13      []
1995-11-20      []
1995-11-27      []
1995-12-04      []
1995-12-11      []
1995-12-18      []
1995-12-25  

In [9]:
totalEarnings = 0
totalCost = 0
totalSPYEarings = 0
totalTime = 0
count = 0
totalPerc = 0
SPYPerc = 0
spy = pd.read_csv('stockData/S&P500.csv').set_index('Date')
for symbol in yf.tickers_sp500():
    df = getStage(symbol)
    inStage = False
    buyTwice = False
    if df.empty:
        continue
    for index, element in df.iterrows():
        index = index.strftime('%Y-%m-%d')
        if element.Stage == "Stage 2" or element.Stage == "Buy":
            transaction.loc[index]['holding'].append((symbol,element.close,0))
            if buyTwice:
                transaction.loc[index]['holding'].append((symbol,element.close,0))
            if element.Stage == "Buy" and inStage:
                transaction.loc[index]['holding'].append((symbol,element.close,0))
                buyTwice = True
            inStage = True
            continue
        if element.Stage == "Sell":
            transaction.loc[index]['holding'].append((symbol,element.close,-1))
            if buyTwice:
                transaction.loc[index]['holding'].append((symbol,element.close,-1))
            inStage = False
            buyTwice = False
    #fullPrint(transaction)


In [25]:
# import cProfile
# cProfile.run('testEfficiency()')

Empty DataFrame
Columns: []
Index: []
Empty DataFrame
Columns: []
Index: []
Empty DataFrame
Columns: []
Index: []
Empty DataFrame
Columns: []
Index: []
Empty DataFrame
Columns: []
Index: []
         3810686480 function calls (3761781161 primitive calls) in 1340.098 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
   595676    1.619    0.000  110.641    0.000 1380679158.py:10(calculateSlope)
        5    0.000    0.000    0.005    0.001 1380679158.py:2(fullPrint)
  1191352    3.799    0.000  246.885    0.000 1380679158.py:5(product)
   595178    2.167    0.000    2.167    0.000 1727823953.py:2(checkIfStage2)
   595178    0.263    0.000    2.430    0.000 1727823953.py:22(checkStage)
        1    1.364    1.364 1340.097 1340.097 2683147906.py:1(testEfficiency)
      503    0.024    0.000  489.237    0.973 2924208062.py:1(returnSortedDf)
   581234    1.445    0.000   92.558    0.000 2924208062.py:10(<lambda>)
   595676    0.543 

In [4]:
transaction.to_pickle("transaction.pkl")
transactionCopy = pd.DataFrame()

In [7]:
transactionCopy = pd.read_pickle('transaction.pkl')
total = 100
prevIndex = ''
first = True
transactionCopy['total'] = 0
for index, element in transactionCopy.iterrows():
    index = index.strftime('%Y-%m-%d')
    if len(element.holding) == 0:
        transactionCopy['total'][index] = total
        continue
    if first:
        first = False
        transactionCopy['total'][index] = total
    else:
        prevData = transactionCopy.loc[prevIndex].holding
        if len(prevData):
            total = 0
            removeList = []
            close = 0
            for i in range(len(prevData)):
                for j in range(len(element.holding)):
                    if element.holding[j][0] == prevData[i][0]:
                        close = element.holding[j][1]
                        if element.holding[j][2] == -1:
                            removeList.append(element.holding[j])
                            print("Sell")
                        break
                total += close*prevData[i][2]
                print(prevData[i][0]+' '+str(close)+' '+str(prevData[i][2])+' '+'total:'+str(total))
            transactionCopy['total'][index] = total
            print('\n')
            for delete in removeList:
                if delete in element.holding:
                    element.holding.remove(delete)
        else:
            transactionCopy['total'][index] = transactionCopy.loc[prevIndex].total
    if len(element.holding):
        allocation = total/len(element.holding)
    for i in range(len(element.holding)):
        element.holding[i] = (element.holding[i][0],element.holding[i][1],allocation/element.holding[i][1])
        print(element.holding[i][0]+' '+str(element.holding[i][1])+' '+str(allocation/element.holding[i][1]))
    print(index+":"+str(total)+'\n')
    prevIndex = index
    
            

    

GILD 2.421875 20.64516129032258
LRCX 18.458332061767578 2.708803798343412
1999-07-26:100

GILD 2.230468988418579 20.64516129032258 total:46.048392018964215
LRCX 18.520832061767578 2.708803798343412 total:96.21769225636068


GILD 2.230468988418579 14.379291643141503
LRCX 18.520832061767578 1.7317021167564455
QCOM 18.46875 1.736585534237756
1999-08-02:96.21769225636068

GILD 2.396483898162842 14.379291643141503 total:34.45974088977612
LRCX 19.854167938232422 1.7317021167564455 total:68.84124553485117
QCOM 20.0 1.736585534237756 total:103.57295621960628


GILD 2.396483898162842 10.804678919291499
LRCX 19.854167938232422 1.304171453342043
QCOM 20.0 1.2946619527450784
XLNX 36.78125 0.7039793116031013
1999-08-09:103.57295621960628

GILD 2.550781011581421 10.804678919291499 total:27.560369823562823
LRCX 16.625 1.304171453342043 total:49.24222023537429
QCOM 21.8671875 1.2946619527450784 total:77.55283590516706
XLNX 36.5 0.7039793116031013 total:103.24808077868026


GILD 2.550781011581421 8.095

In [ ]:
# fullPrint(transactionCopy)
# transactionCopy.to_csv('Testdata/Weekly/Testfull.csv')
transactionCopy.iloc[-1]['total']

                                                      holding         total
1995-01-02                                                 []    100.000000
1995-01-09                                                 []    100.000000
1995-01-16                                                 []    100.000000
1995-01-23                                                 []    100.000000
1995-01-30                                                 []    100.000000
1995-02-06                                                 []    100.000000
1995-02-13                                                 []    100.000000
1995-02-20                                                 []    100.000000
1995-02-27                                                 []    100.000000
1995-03-06                                                 []    100.000000
1995-03-13                                                 []    100.000000
1995-03-20                                                 []    100.000000
1995-03-27  

In [ ]:
printDf = pd.read_pickle('transaction.pkl')
printDf.to_csv('Testdata/Weekly/Transaction.csv')

In [ ]:
fullPrint(transaction)

                                                      holding
Date                                                         
1995-01-06                                                 []
1995-01-13                                                 []
1995-01-20                                                 []
1995-01-27                                                 []
1995-02-03                                                 []
1995-02-10                                                 []
1995-02-17                                                 []
1995-02-24                                                 []
1995-03-03                                                 []
1995-03-10                                                 []
1995-03-17                                                 []
1995-03-24                                                 []
1995-03-31                                                 []
1995-04-07                                                 []
1995-04-